In [1]:
import pandas as pd
import numpy as np
import tqdm
import csv

import torch
from torch.nn import Linear
from torch_geometric.data import Data
from torch_geometric.nn import GCNConv, GATConv
from torch_geometric.explain import Explainer, GNNExplainer

import torch.nn.functional as F

from typing import Dict, List, Optional, Union
from sklearn.manifold import TSNE
import matplotlib.pyplot as plt


In [2]:
feature_names = [
                'age_w1',
                'black',
                'hispanicity',
                'smallnet_w1',
                'education_w1',
                'sexual_identity_w1',
                'past12m_homeless_w1',
                'insurance_type_w1',
                'inconsistent_condom_w1',
                'ever_jailed_w1',
                'freq_3mo_tobacco_w1',
                'freq_3mo_alcohol_w1',
                'freq_3mo_cannabis_w1',
                'freq_3mo_inhalants_w1',
                'freq_3mo_hallucinogens_w1',
                'freq_3mo_stimulants_w1',
                'ever_3mo_depressants_w1',
                'num_sex_partner_drugs_w1',
                'num_nom_sex_w1',
                'num_nom_soc_w1',
                'num_sex_partner_w1',
                'num_oral_partners_w1',
                'num_anal_partners_w1',
                'sex_transact_money_w1',
                'sex_transact_others_w1',
                'depression_sum_w1',

                # graph features
                'sex_cent', 'venue_cent', 'sex_num_neighbor', 'num_social_venues', 'num_health_venues' #'venue_num_neighbor' 
                ]

print(len(feature_names))

31


In [3]:
# load nodes and edges

chicago_counts = 377
houston_counts = 378


n_papers = houston_counts 

nodes = np.load('Nodes_Houston.npy', allow_pickle=True)
edges = pd.read_csv('Edges_Social_Houston.csv')

# nodes = np.load('Nodes_Chicago.npy', allow_pickle=True)
# edges = pd.read_csv('Edges_Social_Chicago.csv')

In [4]:
train_share = 0.75

cut_off = int(n_papers * train_share)
print("train count:", cut_off)
train_mask = n_papers * [False]
train_mask[:cut_off] = cut_off * [True]
test_mask = [not e for e in train_mask]

print("test count:", test_mask.count(1))

train count: 283
test count: 95


In [5]:
df_nodes = pd.DataFrame(nodes, columns =['NodeId', 'labels', 'features'])

In [6]:
df_nodes.head()

NodeId labels                                           features
0      0      0  [0.9611576542269613, 0.0, 1.0, 0.0307692307692...
1      1      0  [0.7395277989337397, 0.0, 0.0, 0.0615384615384...
2      2      0  [0.5719725818735721, 0.0, 1.0, 0.0153846153846...
3      3      0  [0.3945163747143947, 1.0, 0.0, 0.0153846153846...
4      4      0  [0.0, 0.0, 1.0, 0.004615384615384615, 1.0, 1.0...

In [7]:
positive_ids = df_nodes['NodeId'].loc[df_nodes['labels'] == 1]

positive_ids = positive_ids.values
type(positive_ids[0])

int

In [8]:
len(df_nodes['features'][0])

31

In [9]:
_source_node = edges['sourceNodeId'].values
_target_node = edges['targetNodeId'].values

source_node = np.concatenate((_target_node, _source_node))
target_node = np.concatenate((_source_node, _target_node))

In [10]:
x = torch.tensor(
    df_nodes['features'].values.tolist(), dtype=torch.float
    )

y = torch.tensor(
    df_nodes['labels'].values.tolist(), dtype=torch.long
)

edge_index = torch.tensor(np.array([source_node, target_node]), dtype=torch.int64)

graph_object = Data(x=x, edge_index=edge_index, y=y)
graph_object.train_mask = torch.tensor(train_mask)
graph_object.test_mask = torch.tensor(test_mask)

In [11]:
print(graph_object)
print("==============================================================")

print(f"Number of nodes: {graph_object.num_nodes}")
print(f"Number of edges: {int(graph_object.num_edges/2)}")
print(f"Average node degree: {(graph_object.num_edges) / graph_object.num_nodes:.2f}")
print(f"Number of training nodes: {graph_object.train_mask.sum()}")
print(f"Number of test nodes: {graph_object.test_mask.sum()}")
print(f"Training node label rate: {int(graph_object.train_mask.sum()) / graph_object.num_nodes:.2f}")
print(f"Test node label rate: {int(graph_object.test_mask.sum()) / graph_object.num_nodes:.2f}")
print(f"Contains isolated nodes: {graph_object.has_isolated_nodes()}")
print(f"Contains self-loops: {graph_object.has_self_loops()}")
print(f"Is undirected: {graph_object.is_undirected()}")

Data(x=[378, 31], edge_index=[2, 1344], y=[378], train_mask=[378], test_mask=[378])
Number of nodes: 378
Number of edges: 672
Average node degree: 3.56
Number of training nodes: 283
Number of test nodes: 95
Training node label rate: 0.75
Test node label rate: 0.25
Contains isolated nodes: True
Contains self-loops: False
Is undirected: True


In [ ]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(x, y, test_size=0.3, random_state=1)

X_train = X_train.numpy()
X_test = X_test.numpy()
y_train = y_train.numpy()

### GAT Training

In [12]:
# Define accuracy
def accuracy(pred_y, y):
    return (pred_y == y).sum() / len(y)

In [40]:
#GCN

device = 'cpu'

class GCN(torch.nn.Module):
    def __init__(self):
        super().__init__()
        self.gcn = GCNConv(graph_object.num_node_features, 16)
        self.out = Linear(16, len(graph_object.y.unique()))

    def forward(self, x, edge_index):
        h = self.gcn(x, edge_index).relu()
        z = self.out(h)
        return h, z

model = GCN()
print(model)
optimizer = torch.optim.Adam(model.parameters(), lr=0.01)


GCN(
  (gcn): GCNConv(31, 16)
  (out): Linear(in_features=16, out_features=2, bias=True)
)


In [ ]:
## For GCN Training

criterion = torch.nn.CrossEntropyLoss()

# Data for animations
embeddings = []
losses = []
accuracies = []
outputs = []

# Training loop
for epoch in range(2400):
    # Clear gradients
    optimizer.zero_grad()

    # Forward pass
    h,z = model(graph_object.x, graph_object.edge_index)

    # Calculate loss function
    loss = criterion(z[graph_object.train_mask], graph_object.y[graph_object.train_mask])

    # Calculate accuracy
    acc = accuracy(z.argmax(dim=1), graph_object.y)

    # Compute gradients
    loss.backward()

    # Tune parameters
    optimizer.step()

    # Store data for animations
    embeddings.append(h)
    losses.append(loss)
    accuracies.append(acc)
    outputs.append(z.argmax(dim=1))

    # Print metrics every 10 epochs
    if epoch % 10 == 0:
        print(f'Epoch {epoch:>3} | Loss: {loss:.2f} | Acc: {acc*100:.2f}%')

In [13]:
## GAT

device = 'cpu'

class GAT(torch.nn.Module):
    def __init__(self, in_channels, hidden_channels, out_channels, heads):
        super().__init__()
        self.conv1 = GATConv(in_channels, hidden_channels, heads, dropout=0.1)
        # On the Pubmed dataset, use `heads` output heads in `conv2`.
        # self.conv2 = GATConv(hidden_channels * heads, out_channels, heads=1,
        #                      concat=False, dropout=0.6)
        #self.out = Linear(hidden_channels, len(graph_object.y.unique()))

    def forward(self, x, edge_index):
        x = F.dropout(x, p=0.1, training=self.training)
        x = F.relu(self.conv1(x, edge_index))

        return x

model = GAT(graph_object.num_features, 16, len(graph_object.y.unique()),1).to(device)
optimizer = torch.optim.Adam(model.parameters(), lr=0.005, weight_decay=5e-4)

print(model)
#optimizer = torch.optim.Adam(model.parameters(), lr=0.05)

GAT(
  (conv1): GATConv(31, 16, heads=1)
)


In [14]:
## GAT test

#criterion = torch.nn.CrossEntropyLoss()

# Data for animations
embeddings = []
losses = []
accuracies = []
outputs = []


for epoch in range(2400):
    optimizer.zero_grad()

    # Forward pass
    out = model(graph_object.x, graph_object.edge_index)

    loss = F.cross_entropy(out[graph_object.train_mask], graph_object.y[graph_object.train_mask])

    # Calculate accuracy
    acc = accuracy(out.argmax(dim=1), graph_object.y)


    loss.backward()
    optimizer.step()

    losses.append(loss)
    accuracies.append(acc)


    if (epoch+1) % 10 == 0:
        print('Epoch: {}, Loss: {:.4f}, Training Acc: {:.4f}'.format(epoch+1, loss.item(), acc))



Epoch: 10, Loss: 1.9579, Training Acc: 0.5000
Epoch: 20, Loss: 1.3886, Training Acc: 0.6217
Epoch: 30, Loss: 1.1001, Training Acc: 0.6376
Epoch: 40, Loss: 0.9485, Training Acc: 0.5979
Epoch: 50, Loss: 0.8537, Training Acc: 0.6376
Epoch: 60, Loss: 0.7994, Training Acc: 0.6349
Epoch: 70, Loss: 0.7760, Training Acc: 0.6534
Epoch: 80, Loss: 0.6972, Training Acc: 0.6772
Epoch: 90, Loss: 0.7418, Training Acc: 0.6640
Epoch: 100, Loss: 0.7142, Training Acc: 0.6878
Epoch: 110, Loss: 0.6322, Training Acc: 0.7143
Epoch: 120, Loss: 0.6679, Training Acc: 0.7011
Epoch: 130, Loss: 0.6368, Training Acc: 0.7143
Epoch: 140, Loss: 0.6105, Training Acc: 0.6931
Epoch: 150, Loss: 0.6207, Training Acc: 0.7196
Epoch: 160, Loss: 0.6037, Training Acc: 0.7275
Epoch: 170, Loss: 0.5916, Training Acc: 0.7169
Epoch: 180, Loss: 0.5839, Training Acc: 0.7196
Epoch: 190, Loss: 0.5825, Training Acc: 0.7169
Epoch: 200, Loss: 0.5765, Training Acc: 0.7407
Epoch: 210, Loss: 0.5755, Training Acc: 0.7116
Epoch: 220, Loss: 0.53

In [ ]:
# GNN sklearn Metrics
from sklearn.metrics import f1_score, accuracy_score, recall_score, average_precision_score, roc_auc_score  

print('Accuracy: ', accuracy_score(graph_object.y[graph_object.test_mask], z.argmax(dim=1)[graph_object.test_mask]))

print('F1:', f1_score(graph_object.y[graph_object.test_mask], z.argmax(dim=1)[graph_object.test_mask]))

print('Recall:', recall_score(graph_object.y[graph_object.test_mask], z.argmax(dim=1)[graph_object.test_mask]))

print('AUPRC: ', average_precision_score(graph_object.y[graph_object.test_mask], z.argmax(dim=1)[graph_object.test_mask]))

print('AUC: ', roc_auc_score(graph_object.y[graph_object.test_mask], z.argmax(dim=1)[graph_object.test_mask]))


In [ ]:
# GNN PyTorch Metrics
from torcheval.metrics import BinaryAUROC

auc = BinaryAUROC()
precision = Precision(task="multiclass", average='macro', num_classes=2)
f1 = F1Score(task='multiclass', num_classes=2)
recall = BinaryRecall()

print('Accuracy: ', accuracy(z.argmax(dim=1)[graph_object.test_mask], graph_object.y[graph_object.test_mask]))

print('F1:', f1(z.argmax(dim=1)[graph_object.test_mask], graph_object.y[graph_object.test_mask]))

print('Recall:', recall(z.argmax(dim=1)[graph_object.test_mask], graph_object.y[graph_object.test_mask]))

print('Precision: ', precision(z.argmax(dim=1)[graph_object.test_mask], graph_object.y[graph_object.test_mask]))

print('AUC: ', auc.update(z.argmax(dim=1)[graph_object.test_mask], graph_object.y[graph_object.test_mask]).compute())


In [17]:
# GAT sklearn Metrics
from sklearn.metrics import f1_score, accuracy_score, recall_score, precision_score, roc_auc_score  

print('Accuracy: ', accuracy_score(graph_object.y[graph_object.test_mask], out.argmax(dim=1)[graph_object.test_mask]))

print('F1:', f1_score(graph_object.y[graph_object.test_mask], out.argmax(dim=1)[graph_object.test_mask]))

print('Recall:', recall_score(graph_object.y[graph_object.test_mask], out.argmax(dim=1)[graph_object.test_mask]))

print('AUPRC: ', average_precision_score(graph_object.y[graph_object.test_mask], out.argmax(dim=1)[graph_object.test_mask]))

print('AUC: ', roc_auc_score(graph_object.y[graph_object.test_mask], out.argmax(dim=1)[graph_object.test_mask]))


Accuracy:  0.8105263157894737
F1: 0.43749999999999994
Recall: 0.6363636363636364
AUPRC:  0.25422647527910686
AUC:  0.7348484848484848


In [ ]:
# GAT PyTorch metrics

print('Accuracy: ', accuracy(out.argmax(dim=1)[graph_object.test_mask], graph_object.y[graph_object.test_mask]))

print('F1:', f1(out.argmax(dim=1)[graph_object.test_mask], graph_object.y[graph_object.test_mask]))

print('Recall:', recall(out.argmax(dim=1)[graph_object.test_mask], graph_object.y[graph_object.test_mask]))

print('Precision: ', precision(out.argmax(dim=1)[graph_object.test_mask], graph_object.y[graph_object.test_mask]))

print('AUC: ', auc.update(out.argmax(dim=1)[graph_object.test_mask], graph_object.y[graph_object.test_mask]).compute())


In [ ]:
# TSNE Visualization

# Train TSNE
tsne = TSNE(n_components=2, learning_rate='auto', perplexity=5.0, n_iter=5000,
init='pca').fit_transform(out.detach())

# Plot TSNE
plt.figure(figsize=(10, 10))
plt.axis('off')
plt.scatter(tsne[:, 0], tsne[:, 1], s=50, c=graph_object.y)
plt.show()

In [15]:
explainer = Explainer(
    model=model,
    algorithm=GNNExplainer(epochs=1000),
    explanation_type='model',
    node_mask_type='attributes',
    edge_mask_type='object',
    model_config=dict(
        mode='multiclass_classification',
        task_level='node',
        return_type='probs',  # Model returns log probabilities.
    ),
)

In [16]:
def aggregate_feature_importance(
    explanation,
    path: Optional[str] = None,
    feat_labels: Optional[List[str]] = None,
    top_k: Optional[int] = None,
    dictionary: Optional[dict] = None,
):
    
    node_mask = explanation.get('node_mask')
    if node_mask is None:
        raise ValueError(f"The attribute 'node_mask' is not available "
                            f"in '{explanation.__class__.__name__}' "
                            f"(got {explanation.available_explanations})")
    if node_mask.dim() != 2 or node_mask.size(1) <= 1:
        raise ValueError(f"Cannot compute feature importance for "
                            f"object-level 'node_mask' "
                            f"(got shape {node_mask.size()})")

    if feat_labels is None:
        feat_labels = range(node_mask.size(1))

    score = node_mask.sum(dim=0)

    return _aggregate_score(dictionary, score, feat_labels, path)

In [17]:
def _aggregate_score(
    dictionary, 
    score: torch.Tensor,
    labels: List[str],
    path: Optional[str] = None,
    top_k: Optional[int] = None,
):
    import pandas as pd
    from collections import Counter

    if len(labels) != score.numel():
        raise ValueError(f"The number of labels (got {len(labels)}) must "
                         f"match the number of scores (got {score.numel()})")

    score = score.cpu().numpy()

    df = pd.DataFrame({'score': score}, index=labels)
    df = df.sort_values('score', ascending=False)
    df = df.round(decimals=3)

    if top_k is not None:
        df = df.head(top_k)

    output = df['score'].to_dict()

    combine = dict(Counter(dictionary) + Counter(output))
    
    return combine
    

In [18]:
output_agg = {}

total = houston_counts
total_feat = 31
for i in range(total):

    #if i in positive_ids: # add this line if analyzing all vs positive individuals
    explanation = explainer(graph_object.x, graph_object.edge_index, index=i)
    output_agg = aggregate_feature_importance(explanation, dictionary=output_agg, top_k=total_feat, feat_labels = feature_names)

In [20]:
run_num = "annals"

chicago_fname = 'chicago_feature_importance_all_agg_run{}.csv'.format(run_num)
houston_fname = 'houston_feature_importance_all_agg_run{}.csv'.format(run_num)

In [31]:
# sorting feature importance
#Chicago
with open(chicago_fname, 'w') as csv_file:  
    writer = csv.writer(csv_file)
    for key, value in output_agg.items():
       writer.writerow([key, value])

df = pd.read_csv(chicago_fname, header=None)
df = df.sort_values(by=[1], ascending=False)

df.head()

df.to_csv(chicago_fname, index=False)

In [21]:
# Houston
with open(houston_fname, 'w') as csv_file:  
    writer = csv.writer(csv_file)
    for key, value in output_agg.items():
       writer.writerow([key, value])

df = pd.read_csv(houston_fname, header=None)
df = df.sort_values(by=[1], ascending=False)

df.head()

df.to_csv(houston_fname, index=False)

### Barcharts for GNN Feature Importance

In [34]:
# color_dict = {
#     'freq_3mo_alcohol': 'lightcoral',
#     'education': 'darkorange',
#     'venue_num_neighbor': 'gold',
#     'sexual_identity': 'lawngreen',
#     'freq_3mo_cannabis': 'turquoise',
#     'freq_3mo_tobacco': 'deepskyblue',
#     'num_nom_soc': 'violet',
#     'num_sex_partner_drugs': 'pink',
#     'insurance_type': 'palegreen',
#     'age': 'lavender',
#     'num_nom_sex': 'silver',
#     'black': '', 
#     'ever_jailed': '',
# }

#
color_dict_positive_overlap = {
    'freq_3mo_alcohol': 'lightskyblue',
    'education': 'lightskyblue',
    'venue_num_neighbor': 'lightskyblue',
    'sexual_identity': 'lightskyblue',
    'freq_3mo_cannabis': 'lightskyblue',
    'freq_3mo_tobacco': 'lightskyblue',
    'num_nom_soc': 'lightskyblue',
    'insurance_type': 'lightskyblue',      
    'age': 'lightskyblue',                 
    'black': 'lightskyblue', 
    'inconsistent_condom': 'coral',                  # different
    'depression_sum': 'coral'             # different
}

#
color_dict_all_overlap = {
    'freq_3mo_alcohol': 'lightskyblue',
    'education': 'lightskyblue',
    'venue_num_neighbor': 'lightskyblue',
    'sexual_identity': 'lightskyblue',
    'freq_3mo_cannabis': 'lightskyblue',
    'freq_3mo_tobacco': 'lightskyblue',
    'num_nom_soc': 'lightskyblue', 
    'num_sex_partner_drugs': 'coral',     # different
    'insurance_type': 'lightskyblue',            
    'age': 'coral',                       # different
    'num_nom_sex': 'lightskyblue',
    'black': 'lightskyblue'
}

In [29]:
df['Feature Name']

9       depression_sum
8                  age
7          num_nom_soc
6       insurance_type
5                black
4     freq_3mo_tobacco
3    freq_3mo_cannabis
2     freq_3mo_alcohol
1            education
0      sexual_identity
Name: Feature Name, dtype: object

In [26]:
# Chicago All Individuals
import pandas as pd
import matplotlib.pyplot as plt

df = pd.read_csv('/raid/eyu1/Graph_Network_Evan/HIV_data_codes/chicago_feature_importance_all_agg_run_annals.csv', skiprows = 1, names=['Feature Name', 'Aggregate Score'])

#df['score'] = df['score'] / 377 # divide by number of nodes in graph (377 Chicago, 378 Houston)

df = df.iloc[::-1] #reverse order
df = df.iloc[-10:]

df['Aggregate Score'] = df['Aggregate Score'].astype(int)
df['Feature Name'] = df['Feature Name'].str.replace(r'_w1', '', regex=True)# rename column names without w1 label

colors = []

for i, row in df.iterrows():
    colors.append(color_dict_all_overlap[row['Feature Name']])

plt.rcParams["figure.dpi"] = 1200
ax = df.plot.barh(x='Feature Name', y='Aggregate Score', title='GAT Feature Importance for All Chicago Individuals', figsize=(5,10), color = colors)
ax.set(ylabel=None)

# customizing colors according to similar
# ax.get_children()[9].set_color('tab:blue')
# ax.get_children()[8].set_color('lightcoral')
# ax.get_children()[0].set_color('r')

for rect in ax.patches:
    # Find where everything is located
    height = rect.get_height()
    width = rect.get_width()
    x = rect.get_x()
    y = rect.get_y()
    
    # The width of the bar is also not pixels, it's the
    # number of animals. So we can use it as the label!
    label_text = width
    
    # ax.text(x, y, text)
    label_x = x + width - 10
    label_y = y + height / 2
    ax.text(label_x, label_y, label_text, ha='right', va='center', color='black')

In [30]:
# Chicago Positive HIV Individuals
df = pd.read_csv('/raid/eyu1/Graph_Network_Evan/HIV_data_codes/chicago_feature_importance_positive_agg_run_annals.csv', skiprows = 1, names=['Feature Name', 'Aggregate Score'])

df = df.iloc[::-1] #reverse order
df = df.iloc[-10:]

df['Aggregate Score'] = df['Aggregate Score'].astype(int)
df['Feature Name'] = df['Feature Name'].str.replace(r'_w1', '', regex=True)# rename column names without w1 label

plt.rcParams["figure.dpi"] = 1200

colors = []

for i, row in df.iterrows():
    colors.append(color_dict_positive_overlap[row['Feature Name']])

print(colors)

ax = df.plot.barh(x='Feature Name', y='Aggregate Score', title='GAT Feature Importance for All HIV Positive Chicago Individuals', figsize=(5,10), color = colors)
ax.set(ylabel=None)

# .patches is everything inside of the chart, lines and
# rectangles and circles and stuff. In this case we only
# have rectangles!
for rect in ax.patches:
    # Find where everything is located
    height = rect.get_height()
    width = rect.get_width()
    x = rect.get_x()
    y = rect.get_y()
    
    # The width of the bar is also not pixels, it's the
    # number of animals. So we can use it as the label!
    label_text = width
    
    # ax.text(x, y, text)
    label_x = x + width - 10
    label_y = y + height / 2
    ax.text(label_x, label_y, label_text, ha='right', va='center', color='black')

['coral', 'lightskyblue', 'lightskyblue', 'lightskyblue', 'lightskyblue', 'lightskyblue', 'lightskyblue', 'lightskyblue', 'lightskyblue', 'lightskyblue']


In [32]:
# Houston All Individuals
import pandas as pd

df = pd.read_csv('/raid/eyu1/Graph_Network_Evan/HIV_data_codes/houston_feature_importance_all_agg_run_annals.csv', skiprows = 1, names=['Feature Name', 'Aggregate Score'])

df = df.iloc[::-1] #reverse order
df = df.iloc[-10:]

df['Aggregate Score'] = df['Aggregate Score'].astype(int)
df['Feature Name'] = df['Feature Name'].str.replace(r'_w1', '', regex=True)# rename column names without w1 label

plt.rcParams["figure.dpi"] = 1200

colors = []

for i, row in df.iterrows():
    colors.append(color_dict_all_overlap[row['Feature Name']])

ax = df.plot.barh(x='Feature Name', y='Aggregate Score', title='GAT Feature Importance for All Houston Individuals', color = colors, figsize=(5,10))
ax.set(ylabel=None)

# .patches is everything inside of the chart, lines and
# rectangles and circles and stuff. In this case we only
# have rectangles!
for rect in ax.patches:
    # Find where everything is located
    height = rect.get_height()
    width = rect.get_width()
    x = rect.get_x()
    y = rect.get_y()
    
    # The width of the bar is also not pixels, it's the
    # number of animals. So we can use it as the label!
    label_text = width
    
    # ax.text(x, y, text)
    label_x = x + width - 10
    label_y = y + height / 2
    ax.text(label_x, label_y, label_text, ha='right', va='center', color='black')

In [35]:
# Houston Positive HIV Individuals
df = pd.read_csv('/raid/eyu1/Graph_Network_Evan/HIV_data_codes/houston_feature_importance_positive_agg_run_annals.csv', skiprows = 1, names=['Feature Name', 'Aggregate Score'])

df = df.iloc[::-1] #reverse order
df = df.iloc[-10:]

df['Aggregate Score'] = df['Aggregate Score'].astype(int)
df['Feature Name'] = df['Feature Name'].str.replace(r'_w1', '', regex=True)# rename column names without w1 label

plt.rcParams["figure.dpi"] = 1200

colors = []

for i, row in df.iterrows():
    colors.append(color_dict_positive_overlap[row['Feature Name']])

print(colors)

ax = df.plot.barh(x='Feature Name', y='Aggregate Score', title='GAT Feature Importance for All HIV Positive Houston Individuals', color = colors, figsize=(5,10))
ax.set(ylabel=None)

# .patches is everything inside of the chart, lines and
# rectangles and circles and stuff. In this case we only
# have rectangles!
for rect in ax.patches:
    # Find where everything is located
    height = rect.get_height()
    width = rect.get_width()
    x = rect.get_x()
    y = rect.get_y()
    
    # The width of the bar is also not pixels, it's the
    # number of animals. So we can use it as the label!
    label_text = width
    
    # ax.text(x, y, text)
    label_x = x + width - 10
    label_y = y + height / 2
    ax.text(label_x, label_y, label_text, ha='right', va='center', color='black')

['lightskyblue', 'lightskyblue', 'lightskyblue', 'coral', 'lightskyblue', 'lightskyblue', 'lightskyblue', 'lightskyblue', 'lightskyblue', 'lightskyblue']


In [ ]:
df_rename = pd.read_excel('/raid/eyu1/Graph_Network_Evan/HIV_data_codes/ymap_barchart_features_rename.xlsx', header=None)

rename_dict = dict(zip(df_rename.iloc[:,0],df_rename.iloc[:,1]))

In [ ]:
df.replace(rename_dict, regex=True, inplace=True)

df.head()